In [59]:
import pandas as pd
import plotly.graph_objs as go
from sklearn.preprocessing import StandardScaler, MinMaxScaler, RobustScaler

In [60]:
df = pd.read_csv('diet_uk.csv')

In [61]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 72000 entries, 0 to 71999
Data columns (total 24 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   mc_run_id       72000 non-null  int64  
 1   grouping        72000 non-null  object 
 2   mean_ghgs       72000 non-null  float64
 3   mean_land       72000 non-null  float64
 4   mean_watscar    72000 non-null  float64
 5   mean_eut        72000 non-null  float64
 6   mean_ghgs_ch4   72000 non-null  float64
 7   mean_ghgs_n2o   72000 non-null  float64
 8   mean_bio        72000 non-null  float64
 9   mean_watuse     72000 non-null  float64
 10  mean_acid       72000 non-null  float64
 11  sd_ghgs         72000 non-null  float64
 12  sd_land         72000 non-null  float64
 13  sd_watscar      72000 non-null  float64
 14  sd_eut          72000 non-null  float64
 15  sd_ghgs_ch4     72000 non-null  float64
 16  sd_ghgs_n2o     72000 non-null  float64
 17  sd_bio          72000 non-null 

In [62]:

data = df.copy()

data['diet_category'] = df['diet_group'].replace({
    'meat100': 'Heavy Meat Consumption',
    'meat': 'Medium Meat Consumption',
    'meat50': 'Low Meat Consumption',
    'vegan': 'Vegan',
    'veggie': 'Vegetarian',
    'fish': 'Fish'
})

metrics = ['mean_ghgs', 'mean_land', 'mean_watuse', 'mean_watscar', 'mean_bio', 'mean_acid', 'mean_ghgs_ch4',
           'mean_ghgs_n2o']
data_for_chart = data.groupby('diet_category')[metrics].mean().reset_index()
test = data_for_chart.copy()
scaler = StandardScaler()

data_normalized = scaler.fit_transform(data_for_chart[metrics])
data_for_chart[metrics] = data_normalized

In [63]:
fig = go.Figure()

labels = {
    'mean_ghgs': 'GHGs',
    'mean_land': 'Land Use',
    'mean_watuse': 'Water Use',
    'mean_watscar': 'Water Scarcity',
    'mean_bio': 'Biodiversity',
    'mean_acid': 'Acidification',
    'mean_ghgs_ch4': 'GHGs CH4',
    'mean_ghgs_n2o': 'GHGs N2O'
}

for _, row in data_for_chart.iterrows():
    fig.add_trace(go.Scatterpolar(
        r=row[metrics].values,
        theta=[labels[metric] for metric in metrics],  # Map labels
        #fill='toself',
        name=row['diet_category'],

    ))

fig.update_layout(
    polar=dict(
        radialaxis=dict(
            visible=True,
            range=[-3, 3]  # Setting range for Z-scores, typically most data will fall between -3 and 3
        )),
    title="Environmental Impact by Diet (Z-Score Normalized Metrics)",

)

fig.show()

In [64]:
scaler = MinMaxScaler()
metrics = ['mean_ghgs', 'mean_land', 'mean_watuse', 'mean_watscar', 'mean_bio', 'mean_acid', 'mean_ghgs_ch4',
           'mean_ghgs_n2o']
df[metrics] = scaler.fit_transform(df[metrics])

df['mean_abs_scaled_metrics'] = df[metrics].abs().mean(axis=1)

max_mean_abs_scaled_metrics = df['mean_abs_scaled_metrics'].max()
df['environmental_impact_percent'] = (df['mean_abs_scaled_metrics'] / max_mean_abs_scaled_metrics) * 100

In [65]:
import plotly.express as px

data = df.copy()

data['diet_category'] = df['diet_group'].replace({
    'meat100': 'Meat',
    'meat': 'Meat',
    'meat50': 'Meat',
    'vegan': 'Vegan',
    'vegetarian': 'Vegetarian',
    'fish': 'Fish'
})

data['diet_sub_category'] = data['diet_group'].apply(lambda x: x if 'meat' in x else 'Mixed')
data['diet_sub_category'] = data['diet_sub_category'].replace({
    'meat100': 'High Consumption',
    'meat50': 'Low Consumption',
    'meat': 'Medium Consumption'
})

fig = px.treemap(data
                 , path=['diet_category', 'diet_sub_category', 'age_group', 'sex'], values='environmental_impact_percent',
                 color='environmental_impact_percent', title='Environmental by Diet Type and Intensity',
                 labels={'environmental_impact_percent': 'Relative Environmental Impact (%)'},
                 color_continuous_scale='YlOrRd',
                 )
fig.update_traces(marker=dict(cornerradius=5))
fig.show()


In [66]:
fig = px.box(data, y='diet_category', x='environmental_impact_percent', color='diet_category',
             title='Environmental Impact by Diet Group',
             labels={'environmental_impact_percent': 'Relative Environmental Impact (%)',
                     'diet_category': 'Diet Category'},
             color_discrete_map={'meat100': 'red', 'meat': 'orange', 'meat50': 'yellow', 'vegan': 'green',
                                 'veggie': 'blue', 'fish': 'purple'}
             )
fig.show()